In [1]:
%load_ext sql
%sql sqlite://

'Connected: None@None'

Set Operators
=======
We generate three tables below:
* R is {1,2,3,4,5}
* S is {}
* T is {1,4,7,10}


In [2]:
# Create tables & insert some random numbers
# Note: in Postgresql, try the generate_series function...
%sql DROP TABLE IF EXISTS R; DROP TABLE IF EXISTS S; DROP TABLE IF EXISTS T;
%sql CREATE TABLE R (A int); CREATE TABLE S (A int); CREATE TABLE T (A int);
for i in range(1,6):
    %sql INSERT INTO R VALUES (:i)
for i in range(1,11,3):
    %sql INSERT INTO T VALUES (:i)

Done.
Done.
Done.
Done.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.


Let's try to get $R \cap (S \cup T) = (R \cap S) \cup (R \cap T)=\{1,4\}$

In [23]:
%%sql SELECT DISTINCT R.A FROM R, S, T
WHERE R.A=S.A OR R.A=T.A

Done.


[]

In [3]:
%sql SELECT * FROM R, S, T;

Done.


[]

**Why is the return set empty?**

*Recall the order of operations for this query:*
1. We take the cross-product of `R,S,T`
2. We filter this intermediate table by the conditions of the `WHERE` clause.  

Let's see (1):

In [24]:
%sql SELECT DISTINCT R.A FROM R, S, T;

Done.


[]

The cross-product query is empty because `S` is empty!

Union
-----

Let's try a different way using a new SQL command, `UNION`:

In [4]:
%%sql
SELECT R.A FROM R, S WHERE R.A=S.A
UNION -- this is an explicit keyword!
SELECT R.A FROM R, T WHERE R.A=T.A

Done.


[(1,), (4,)]

* There are no duplicates (union is a set)
* If we wanted duplicates, we could use UNION ALL
  * R = {1,2,3,4,5}
  * S = {1,2,3,4,5}
  * T = {1,4,7,10}

In [5]:
%sql DROP TABLE IF EXISTS S; CREATE TABLE S (A int);
for i in range(1,6):
    %sql INSERT INTO S VALUES (:i)

Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.


In [6]:
%%sql
-- UNION ALL example- notice that 1 and 4 occur twice!
SELECT R.A FROM R, S WHERE R.A=S.A
UNION ALL
SELECT R.A FROM R, T WHERE R.A=T.A

Done.


[(1,), (2,), (3,), (4,), (5,), (1,), (4,)]

Other Set Operations: INTERSECT, EXCEPT
-------------------------------------

Two examples below... see more in the next section

In [28]:
%%sql
SELECT R.A FROM R, S, T WHERE R.A = S.A
INTERSECT
SELECT R.A FROM R, S, T WHERE R.A = T.A

Done.


[(1,), (4,)]

In [29]:
%%sql
SELECT R.A FROM R, S, T WHERE R.A = S.A
EXCEPT
SELECT R.A FROM R, S, T WHERE R.A = T.A

Done.


[(2,), (3,), (5,)]

In [8]:
%sql DROP TABLE IF EXISTS R; DROP TABLE IF EXISTS S; DROP TABLE IF EXISTS T;
%sql CREATE TABLE R (A int); CREATE TABLE S (A int); CREATE TABLE T (A int);
for i in range(1,6):
    %sql INSERT INTO R VALUES (:i)
for i in range(1,11,3):
    %sql INSERT INTO T VALUES (:i)

Done.
Done.
Done.
Done.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.


In [10]:
% sql SELECT * FROM T WHERE T.A IN (SELECT R.A FROM R);

Done.


[(1,), (4,)]

Nested queries
========

Instead, let's see one solution to the above problem that uses *nested queries*: i.e. subqueries that return relations which our main query then operates over:

We can also use the following over the results of nested subqueries:
* `IN`
* `ALL`
* `ANY`
* `EXISTS`

**Unfortunately, `ALL` and `ANY` are not supported in SQLite. 

Aggregation
=======

SQL supports several aggregation operations:
* `SUM`
* `COUNT`
* `AVG`
* `MIN`
* `MAX`

*Except `COUNT`*, all aggregation operators apply to a single attribute only

In [11]:
%sql DROP TABLE IF EXISTS S; CREATE TABLE S (A int, B int);
for i in range(2,21,2):
    j = i + 1;
    k = i + 2;
    %sql INSERT INTO S VALUES (:i, :i)
    %sql INSERT INTO S VALUES (:i, :j)
    %sql INSERT INTO S VALUES (:j, :j)

%sql select * from S;

Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
Done.


[(2, 2),
 (2, 3),
 (3, 3),
 (4, 4),
 (4, 5),
 (5, 5),
 (6, 6),
 (6, 7),
 (7, 7),
 (8, 8),
 (8, 9),
 (9, 9),
 (10, 10),
 (10, 11),
 (11, 11),
 (12, 12),
 (12, 13),
 (13, 13),
 (14, 14),
 (14, 15),
 (15, 15),
 (16, 16),
 (16, 17),
 (17, 17),
 (18, 18),
 (18, 19),
 (19, 19),
 (20, 20),
 (20, 21),
 (21, 21)]

Here are some simple examples:

In [12]:
%sql SELECT AVG(A), COUNT(A) AS Total, MIN(A), MAX(A), SUM(A) FROM S;

Done.


[(11.333333333333334, 30, 2, 21, 340)]

In [13]:
%sql SELECT  COUNT(DISTINCT A)  FROM S 

Done.


[(20,)]

In [60]:
%sql SELECT  SUM(B)  FROM S 

Done.


[(115,)]

In [15]:
%sql SELECT  A, B, SUM(B)  FROM S GROUP BY A;

Done.


[(2, 3, 5),
 (3, 3, 3),
 (4, 5, 9),
 (5, 5, 5),
 (6, 7, 13),
 (7, 7, 7),
 (8, 9, 17),
 (9, 9, 9),
 (10, 11, 21),
 (11, 11, 11),
 (12, 13, 25),
 (13, 13, 13),
 (14, 15, 29),
 (15, 15, 15),
 (16, 17, 33),
 (17, 17, 17),
 (18, 19, 37),
 (19, 19, 19),
 (20, 21, 41),
 (21, 21, 21)]

In [16]:
%sql SELECT  A,SUM(B), COUNT(A)  FROM S GROUP BY A;

Done.


[(2, 5, 2),
 (3, 3, 1),
 (4, 9, 2),
 (5, 5, 1),
 (6, 13, 2),
 (7, 7, 1),
 (8, 17, 2),
 (9, 9, 1),
 (10, 21, 2),
 (11, 11, 1),
 (12, 25, 2),
 (13, 13, 1),
 (14, 29, 2),
 (15, 15, 1),
 (16, 33, 2),
 (17, 17, 1),
 (18, 37, 2),
 (19, 19, 1),
 (20, 41, 2),
 (21, 21, 1)]

In [21]:
%sql SELECT  A, SUM(B) AS X  FROM S GROUP BY A HAVING (X < 20) AND (A % 2 = 0) ;

Done.


[(2, 5), (4, 9), (6, 13), (8, 17)]

NULL values in SQL
-----------------

Let's look at an odd pair of queries:

In [22]:
%%sql DROP TABLE IF EXISTS bagel;
CREATE TABLE bagel (name TEXT, price MONEY, made_by TEXT);
INSERT INTO bagel VALUES ('Plain with shmear', 1.99, 'Bobs Bagels');
INSERT INTO bagel VALUES ('Egg with shmear', 2.39, 'Bobs Bagels');
INSERT INTO bagel VALUES ('eBagel Drinkable Bagel', 27.99, 'eBagel');
INSERT INTO bagel VALUES ('eBagel Expansion Pack', 1.99, 'eBagel');
INSERT INTO bagel VALUES ('Plain with shmear', 0.99, 'BAGEL CORP');
INSERT INTO bagel VALUES ('Organic Flax-seed bagel chips', 0.99, 'BAGEL CORP');

DROP TABLE IF EXISTS purchase;
-- Note that date is an int here just to simplify things
CREATE TABLE purchase (bagel_name TEXT, franchise TEXT, date INT, quantity INT, purchaser_age INT);
INSERT INTO purchase VALUES ('Plain with shmear', 'Bobs Bagels', 1, 12, 28);
INSERT INTO purchase VALUES ('Egg with shmear', 'Bobs Bagels', 2, 6, 47);
INSERT INTO purchase VALUES ('Plain with shmear', 'BAGEL CORP', 2, 12, 24);
INSERT INTO purchase VALUES ('Plain with shmear', 'BAGEL CORP', 3, 1, 17);
INSERT INTO purchase VALUES ('eBagel Expansion Pack', 'eBagel', 1, 137, 5);
INSERT INTO purchase VALUES ('Plain with shmear', 'Bobs Bagels', 4, 24, NULL);

SELECT * FROM purchase WHERE bagel_name LIKE '%shmear%';

Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
Done.
Done.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
1 rows affected.
Done.


[('Plain with shmear', 'Bobs Bagels', 1, 12, 28),
 ('Egg with shmear', 'Bobs Bagels', 2, 6, 47),
 ('Plain with shmear', 'BAGEL CORP', 2, 12, 24),
 ('Plain with shmear', 'BAGEL CORP', 3, 1, 17),
 ('Plain with shmear', 'Bobs Bagels', 4, 24, None)]

In [23]:
%sql SELECT * FROM bagel ;

Done.


[('Plain with shmear', 1.99, 'Bobs Bagels'),
 ('Egg with shmear', 2.39, 'Bobs Bagels'),
 ('eBagel Drinkable Bagel', 27.99, 'eBagel'),
 ('eBagel Expansion Pack', 1.99, 'eBagel'),
 ('Plain with shmear', 0.99, 'BAGEL CORP'),
 ('Organic Flax-seed bagel chips', 0.99, 'BAGEL CORP')]

In [24]:
%sql SELECT * FROM purchase; 

Done.


[('Plain with shmear', 'Bobs Bagels', 1, 12, 28),
 ('Egg with shmear', 'Bobs Bagels', 2, 6, 47),
 ('Plain with shmear', 'BAGEL CORP', 2, 12, 24),
 ('Plain with shmear', 'BAGEL CORP', 3, 1, 17),
 ('eBagel Expansion Pack', 'eBagel', 1, 137, 5),
 ('Plain with shmear', 'Bobs Bagels', 4, 24, None)]

In [25]:
%%sql SELECT * FROM purchase 
WHERE bagel_name LIKE '%shmear%' 
  AND (purchaser_age >= 5 OR purchaser_age < 5);

Done.


[('Plain with shmear', 'Bobs Bagels', 1, 12, 28),
 ('Egg with shmear', 'Bobs Bagels', 2, 6, 47),
 ('Plain with shmear', 'BAGEL CORP', 2, 12, 24),
 ('Plain with shmear', 'BAGEL CORP', 3, 1, 17)]

We see that `NULL` values are treated specially.  In SQL, there are actually three effective boolean values- `TRUE`, `FALSE`, and `UNKNOWN`.  Any comparison operation between a `NULL` value and a constant will return `UNKNOWN`- and in SQL, relations are only passed through when the condition over them returns `TRUE`.  We can of course handle them specially though:

In [28]:
%%sql SELECT * FROM purchase
WHERE bagel_name LIKE '%shmear%'
  AND (purchaser_age >= 5 OR purchaser_age < 5 
       OR purchaser_age IS NULL);

Done.


[('Plain with shmear', 'Bobs Bagels', 1, 12, 28),
 ('Egg with shmear', 'Bobs Bagels', 2, 6, 47),
 ('Plain with shmear', 'BAGEL CORP', 2, 12, 24),
 ('Plain with shmear', 'BAGEL CORP', 3, 1, 17),
 ('Plain with shmear', 'Bobs Bagels', 4, 24, None)]

What happens when there are nulls in a join?

In [16]:
%%sql 
SELECT * 
FROM bagel b, purchase p where b.name = p.bagel_name;

Done.


[('Plain with shmear', 1.99, 'Bobs Bagels', 'Plain with shmear', 'BAGEL CORP', 2, 12, 24),
 ('Plain with shmear', 1.99, 'Bobs Bagels', 'Plain with shmear', 'BAGEL CORP', 3, 1, 17),
 ('Plain with shmear', 1.99, 'Bobs Bagels', 'Plain with shmear', 'Bobs Bagels', 1, 12, 28),
 ('Plain with shmear', 1.99, 'Bobs Bagels', 'Plain with shmear', 'Bobs Bagels', 4, 24, None),
 ('Egg with shmear', 2.39, 'Bobs Bagels', 'Egg with shmear', 'Bobs Bagels', 2, 6, 47),
 ('eBagel Expansion Pack', 1.99, 'eBagel', 'eBagel Expansion Pack', 'eBagel', 1, 137, 5),
 ('Plain with shmear', 0.99, 'BAGEL CORP', 'Plain with shmear', 'BAGEL CORP', 2, 12, 24),
 ('Plain with shmear', 0.99, 'BAGEL CORP', 'Plain with shmear', 'BAGEL CORP', 3, 1, 17),
 ('Plain with shmear', 0.99, 'BAGEL CORP', 'Plain with shmear', 'Bobs Bagels', 1, 12, 28),
 ('Plain with shmear', 0.99, 'BAGEL CORP', 'Plain with shmear', 'Bobs Bagels', 4, 24, None)]

In [7]:
%%sql 
SELECT DISTINCT b.name 
FROM bagel b, purchase p 
WHERE b.name = p.bagel_name AND b.made_by = p.franchise;

Done.


[('Plain with shmear',), ('Egg with shmear',), ('eBagel Expansion Pack',)]

We're missing bagels which were never purchased!

Inner and Outer Joins
--------------------

A join query using a `WHERE` clause like the one just showed is actually an `INNER JOIN`, and can also be written as follows:

In [42]:
%%sql 
SELECT DISTINCT b.name 
FROM bagel b
    INNER JOIN purchase p ON b.name = p.bagel_name AND b.made_by = p.franchise;

Done.


[(u'Plain with shmear',), (u'Egg with shmear',), (u'eBagel Expansion Pack',)]

An `INNER JOIN` on tables `A` and `B` with join condition `C(A,B)` returns only relations `(a,b)` such that `C(a,b) = TRUE`.  If, as in our example above, there is no `b` such that `C(a,b)` is true, then `a` is simply not returned in thr output multiset.

We can use an `OUTER JOIN` instead, however, which comes in three varieties: `LEFT`, `RIGHT`, and `FULL`. 

In our current situation, what we needed was a `LEFT OUTER JOIN`.  A left outer join will also return `(a, NULL)` for left relations `a` such that there is no `b` for which `C(a,b) = TRUE`:

In [43]:
%%sql 
SELECT DISTINCT b.name 
FROM bagel b
    LEFT OUTER JOIN purchase p ON b.name = p.bagel_name AND b.made_by = p.franchise;

Done.


[(u'Plain with shmear',),
 (u'Egg with shmear',),
 (u'eBagel Drinkable Bagel',),
 (u'eBagel Expansion Pack',),
 (u'Organic Flax-seed bagel chips',)]